# Implémenter des réseaux de neurones avec Keras

## Introduction

### Installation

Avant toute chose, nous devons installer `keras` et `tensorflow` (déjà fait sur colab), si possible avec conda (sinon avec pip). Puis vérifier le succès de l'installation avec le code ci-dessous :

In [0]:
import keras
import numpy as np
np.set_printoptions(formatter={'float': lambda x: "%.3f"%x}) # Pour n'afficher que 4 chiffres

# Cacher les warnings
import warnings
warnings.filterwarnings('ignore')

print("Version de keras", keras.__version__)

## Les limites des méthodes classiques de machine learning

### Le dataset MNIST

Le problème des iris traité avec `scikit-learn` était un problème relativement simple, puisque les caractéristiques (features) d'un iris pouvaient se ramener à seulement 4 valeurs, qui permettaient très facilement de les identifier (séparation visible à l'oeil nu)

Bien entendu, ce n'est pas toujours le cas. Pour s'en rendre compte, nous allons prendre l'exemple de la reconnaissance de chiffres, avec le très connu dataset **MNIST**. C'est un ensemble d'images 28x28 avec les chiffres correspondants :

![MNIST](https://upload.wikimedia.org/wikipedia/commons/2/27/MnistExamples.png )

Voyons comment est composé ce dataset :

In [0]:
from keras.datasets import mnist
import matplotlib.pyplot as plt

(X_train, y_train), (X_test, y_test) = mnist.load_data()

print("Shape des features", X_train.shape)
print("Shape des labels", y_train.shape)

print("Label première image :", y_train[0])
print("Première image :")
plt.imshow(X_train[0])

Ce dataset est donc consitué d'images de 28 par 28 auxquelles sont associés le chiffre correspondant (label). Comment peut-on entrainer un modèle sur des images ? 

Dans la majorité des modèles, les features sont des nombres. Pour décrire cette image, on a donc besoin de 28 x 28 = 784 entrées. Changeons la forme des données d'entrée pour s'adapter à cette représentation.

In [0]:
print("Shape des features", X_train.shape)

X_train, X_test = X_train.reshape(-1, 784), X_test.reshape(-1, 784)

print("Nouvelle shape des features", X_train.shape)

### Trouver des modèles adaptés

Pour le dataset des iris, nous n'avions que 4 features au lieu de 784, et 130 données d'entrée au lieu de 60000. On passe donc à une toute autre échelle, et il devient très compliqué d'imaginer une représentation de l'ensemble des données. Les algorithmes tels que k-NN et SVC deviennent dificilement utilisable face à la grande quantité de données (ils doivent en effet "retenir" certaines données, ce qui est trop coûteux notamment en terme de mémoire). 

Il faut donc utiliser des modèles ne reposant pas sur des données à mémoriser, mais sur un modèle pré-défini dont les paramètres sont à optimiser. On s'écarte alors des méthodes de classification classiques : de tels modèles sont des **modèles de régression**.

C'est par exemple le cas du Naive Bayes, qui mémorise simplement une distribution de probabilités dont le modèle est prédéfini mais les paramètres restent à déterminer (espérance, variance...).

In [0]:
from sklearn.naive_bayes import GaussianNB
from sklearn.metrics import accuracy_score

model_svc = GaussianNB()

#Entrainer le modèle avec la fonction fit et les données X_train et y_train
model_svc.fit(X_train, y_train)

y_pred = model_svc.predict(X_test)

print("Précision :", accuracy_score(y_pred, y_test))

On remarque qu'il ne parvient pas à de fabuleux résultats ici. C'est un modèle très limité par sa définition, il ne peut pas modéliser des choses complexes. Pour avoir plus de flexibilité, on va se tourner vers des modèles de régression.

### Rappel sur le passage de classification à régression

On doit transformer les labels qui sont des entiers en **sparse vector** ou **one-hot**, c'est à dire en vecteurs de la forme $(0, 0, 1, 0, ..., 0)$. L'étiquettage des images par l'entier qu'elles représentent n'est pas satisfaisant car elle introduit une notion de distance qui peut induire le modèle en erreur : il n'est pas pire de confondre un 0 avec un 8 qu'un 0 avec un 1. On transforme donc le chiffre en un vecteur de 10 valeurs distinctes, avec un 1 à l'indice correspondant au chiffre.

### Utiliser les régressions de sci-kit learn

In [0]:
from sklearn.preprocessing import OneHotEncoder

y_train = y_train.reshape(-1, 1)
y_test = y_test.reshape(-1, 1)

print("Labels shape :", y_train.shape)

enc = OneHotEncoder(categories=np.arange(10).reshape(1,-1))

enc.fit(y_train)
y_train, y_test = enc.transform(y_train).toarray(), enc.transform(y_test).toarray()

print("Labels new shape :", y_train.shape)

A présent, quel modèle prendre ? On souhaite, à partir des valeurs des pixels, obtenir une probabilité pour chaque nombre. Essayons de trouver une relation linéaire.

In [6]:
from sklearn.linear_model import LinearRegression

# Création du modèle
model_linear = LinearRegression()

# Entrainement
model_linear.fit(X_train, y_train)

# Prédiction
#Prédire les classes des X_test avec predict
y_logits = model_linear.predict(X_test)
y_pred = enc.inverse_transform(y_logits) # Déduction des classes prédites

# Evaluation du modèle
print("Valeurs prédites :\n", y_logits[:3])
print("Prédictions correspondantes :\n", y_pred[:3])
print("Précision :", accuracy_score(y_pred, enc.inverse_transform(y_test)))

Valeurs prédites :
 [[0.028 0.004 0.103 0.104 -0.121 -0.011 -0.015 0.905 -0.080 0.083]
 [0.221 -0.228 0.830 0.097 -0.335 0.202 0.358 -0.029 -0.032 -0.086]
 [0.041 0.747 0.042 0.005 0.070 0.044 0.032 0.058 -0.062 0.021]]
Prédictions correspondantes :
 [[7]
 [2]
 [1]]
Précision : 0.8593


Pour que les valeurs en sortie soient comprises entre 0 et 1 par la nature du modèle, et que la fonction perte ait plus de sens, on peut rajouter la fonction logistique à la fin de chaque sortie. Un tel modèle existe sur sci-kit (il s'utilise un peu différemment).

**Attention** l'entrainement de ce modèle est assez long, ne l'exécutez que si vous avez un ordi assez puissant et que vous n'êtes pas pressé ! (quelques minutes)

In [0]:
from sklearn.linear_model import LogisticRegression

# Création du modèle
model_logistic = LogisticRegression(solver='lbfgs', multi_class='multinomial', max_iter=1000)

# Entrainement
model_logistic.fit(X_train, enc.inverse_transform(y_train))

# Prédiction
y_logits = model_logistic.predict_proba(X_test)
y_pred = enc.inverse_transform(y_logits) # Déduction des classes prédites

# Evaluation
print("Valeurs prédites :\n", y_logits[:3])
print("Prédictions correspondantes :\n", y_pred[:3])
print("Précision :", accuracy_score((y_pred), (enc.inverse_transform(y_test))))

Ce modèle fonctionne relativement bien. Il permet d'obtenir une probabilité pour une classe donnée en affectant un poids à chaque pixel puis une fonction d'activation. 

En revanche, le modèle ne peut avoir qu'un degré d'abstraction. Il regarde les pixels individuellement sans pouvoir tenir compte des autres. On peut d'ailleurs regarder le poids qu'il affecte à chaque pixel sur un plan. (on ajoute du flou pour mieux voir les tendances globales)

In [0]:
from scipy.ndimage.filters import gaussian_filter

weights = model_logistic.coef_.reshape(-1, 28, 28)

plt.imshow(gaussian_filter(weights[7], 1), cmap='bwr', vmin=-0.02, vmax=0.02)

Comme le modèle ne permet pas d'analyser plusieurs pixels simultanément, il ne peut pas détecter de traits, de cercles etc. Il s'accorche donc à ce qu'il peut, c'est à dire principalement aux extrémités.

Pour pouvoir détecter ces différentes formes, il faut rajouter des degrés d'abstraction. C'est ici qu'intervient le réseau de neurones...

## Votre premier réseau de neurones

### Pourquoi Keras ?

Dans le domaine de l'IA, il existe beaucoup de bibliothèques. En ce qui concerne les réseaux de neurones en python, trois se distinguent :

- **Tensorflow**, développé par Google depuis 3 ans, est probablement la plus utilisée. Cette bibliothèque a notamment permis la réalisation d'AlphaGo puis Alpha Zero.
- **Theano**, développé par l'université de Montréal, est également populaire. Elle est une sorte de numpy adaptée aux réseaux de neurones.
- **Pytorch**, développée par Facebook sepuis seulement 2 ans est également en train de prendre une place importante dans le domaine.

Pourquoi n'y a-t-il pas Keras ? L'objectif de ces bibliothèques est de fournir tous les outils nécessaires à la mise en place d'à peu près n'importe quel réseau de neurone de façon optimisée en implémentant les algorithmes les plus utilisés. Des dizaines d'optimiseurs, de fonctions d'évaluation, de fonctions pertes sont implémentées et fonctionnent ensemble naturellement. On peut donc tout faire avec ces bibliothèques sans se préocupper de l'implémentations des algorithmes et de leur optimisation. C'est donc un socle indispensable relativement **bas niveau**.

En revanche, lorsqu'on souhaite implémenter un réseau de neurone classique, il est nécessaire de le décrire intégralement, ce qui peut être long et répétitif. C'est pourquoi Keras est apparu. C'est une bibliothèque plus **haut niveau** qui est en fait une sur-couche basée sur TensorFlow ou Theano (il y a aussi CNTK et d'autres arrivent). Elle permet de mettre en place des réseaux de neurones très variés (mais de structure classique) très rapidement.

### Rappel sur les neurones

Un neurone artificiel est en fait une fonction qui prend des arguments en entrée $x_1, ..., x_n$ et renvoie une sortie $y_1$.

Cette fonction est une somme pondérée des entrées plus un biais, à laquelle on applique une fonction d'activation : 

$$y_1 = a(\sum(w_ix_i) + b)$$

L'intérêt réside dans le fait que les poids sont variables, que la fonction finale est non linéaire et dérivable (par rapport aux poids). Ainsi, en connectant des neurones entre eux, on peut créer des fonctions complexes que l'on peut optimiser par *gradient descent*.

![Nerone](https://cdn-images-1.medium.com/max/800/1*FcEfcrucAFymCr0gMFQ0QA@2x.png)

Un neurone est en fait une fonction qui renvoie la somme pondérée de ses entrées, le tout passant dans une *fonction d'activation*. Les **fonctions d'activation** les plus utilisées sont la *sigmoïde* et le *ReLU* (Rectified Linear Unit)

![Activations](https://cdn-images-1.medium.com/max/1600/1*XxxiA0jJvPrHEJHD4z893g.png)

### Modèle séquentiel, couches denses

Voici la structure d'un réseau de neurones classique, dit feed-forward.

![Couches](https://cdn-images-1.medium.com/max/800/1*Gh5PS4R_A5drl5ebd_gNrg@2x.png)

On remarque qu'il est constitué de couches qui se succèdent les unes aux autres. Un tel modèle est appelé modèle **séquentiel**.

On remarque également que pour chaque couche, tous les neurones sont connectés aux couches adjacentes. On dit que ces couches sont **denses**.

### Implémentation

Commençont par implémenter le modèle `logistic` réalisé avec sci-kit. Celui-ci correspond en fait à un modèle **séquentiel** composé de :

- une entrée de taille $28\times 28 = 784$
- une **couche dense** de sortie de taille $10$, avec pour fonction d'activation une **sigmoide** (aussi appelée fonction logistique). En réalité, pour que la somme des sorties valent toujours 1, on utilise **softmax** au lieu de la sigmoide, mais la fonction sous-jacente est la même.

Voici donc le code correspondant sur Keras permettant de créer le modèle :

In [0]:
import keras

# Création du modèle séquentiel
model = keras.models.Sequential()

# Ajout d'une couche dense de taille 10 ayant une entrée de taille 784 et une fonction d'activation sigmoide.
model.add(keras.layers.Dense(10, input_dim=784, activation='softmax'))

# Visualiser le modèle qu'on a créé (facultatif)
model.summary()

La forme de notre modèle est ainsi créée, avec des paramètres qui pourront être entrainés pour obtenir la fonction permettant de réaliser la tache souhaitée.

### Entrainement

A présent, il faut dire comment on veut entrainer notre réseau de neurone. Pour cela il faut choisir :

- Une **fonction coût**, qui va devoir être minimisée. Quand on fait de la classification, la meilleure est `categorical_crossentropy`. Quand on fait de la régression, il vaut mieux `mean_squared_error`.
- Un **optimiseur**. La descente de gradient est très compliquée quand on a beaucoup de paramètres à entrainer (ici notre réseau de neurones évolue dans un espace de dimension 7850, quand notre régression linéaire évoluait dans un espace de dimension 2). Il est donc important d'avoir un optimiseur très performant, capable d'explorer l'espace efficacement sans rester coincé dans un minimum local. L'optimiseur utilisé dans la majorité des cas est `adam`.
- Des **métriques** (facultatif). On va ici regarder la précision.

Ensuite, le modèle fonctionne de la même façon qu'un modèle sci-kit learn.

In [0]:
# Compilation du modèle pour le préparer à l'entrainement
model.compile(optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])

# Entrainer le réseau
< Compléter >

# Prédire les sorties
< Compléter >

# Afficher les prédictions
print("Prédictions :")
< Compléter >

# Calculer la précision (évaluer les métriques)
accuracy = model.evaluate(X_test, y_test)[1]
print("Précision : %.2f" % accuracy)

On obtient une précision bien moins bonne que dans le modèle scikit-learn. Pourquoi ?

Avec sci-kit learn, le modèle proposé était tout prêt, alors qu'ici on a du le recréer. On a donc probablement dû oublier quelque chose dans notre modèle. En effet, il s'agit de la **normalisation**.

## Normalisation

Si on regarde notre jeu de données, on s'apperçoit que les valeurs en X sont entre 0 et 255. Or, les algorithmes d'entrainement des réseaux de neurones sont faits pour des données normalisées, c'est à dire dont la moyenne est d'environ 0 et l'écart-type de 1. On doit donc normaliser nos données. Par chance, il existe une couche (layer) de keras qui s'en charge pour nous. Cette couche est `keras.layers.BatchNormalization` et doit être la première couche du modèle, c'est donc elle qui doit prendre les entrées avec l'argument `input_shape=(784,)`. Voir la [documentation](https://keras.io/layers/normalization/) si besoin et l'implémenter ci-dessous :

In [0]:
# Création du modèle séquentiel
model = keras.models.Sequential()

# Ajout de la couche de normalisation et de la couche Dense.
model.add(keras.layers.BatchNormalization(input_shape=(784,)))
# ajouter au modèle la couche keras.layers.Dense(10, activation='softmax')
< Compléter >

# Compiler le modèle
model.compile(optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])

# # Entrainer le réseau
model.fit(X_train, y_train)

# # Evaluer le réseau
accuracy = model.evaluate(X_test, y_test)[1]
print("Précision : %.2f" % accuracy)

Notre précision a bien augmenté, mais on n'est toujours pas au niveau attendu. D'ailleurs, l'entrainement avec scikit était plus long. Pourquoi ?

## Paramètres d'entrainement

Une fois le bon modèle choisi, il faut l'entrainer. Et entraîner un réseau de neurones est compliqué. Une fois la méthode d'entrainement choisie (fonction cout et optimiseur), il reste à déterminer beaucoup de choses, dont notamment :

- Avec combien de données l'entraîner ?
- Quand mettre à jour les poids ?

### Les batchs

Pour cela, on sépare le jeu de données d'entraînement en **batch**. Un batch est un ensemble de données pour lequel on va calculer la fonction coût, calculer le gradient et mettre à jour les poids. En effet, on ne peut pas le faire avec toutes les données à la fois car cela prendrait trop de temps pour une seule itération. En revanche, si on ne prend qu'une valeur à la fois (déscente stochastique), on sera trop éloigné du gradient réel à chaque itération. Il faut donc trouver un compromis, qui est le *batch*, un groupe de points pour lesquels on évalue le *gradient moyen*.

![Batch](https://cdn-images-1.medium.com/max/1600/1*PV-fcUsNlD9EgTIc61h-Ig.png)

Par défaut, sa valeur est fixée à 32 mais on peut la faire varier si besoin. Il s'agit de trouver un compromis entre **vitesse d'entrainement** et **stabilité**. Plus les données d'entrées sont complexes, et variées, plus il est nécessaire d'avoir de grands batchs.

Ici pour stabiliser l'entrainement sur la fin, on va augmenter la taille des batchs à 128.

### Les époques

En l'occurence, l'entraînement s'est déroulé assez vite et la fonction perte semblait diminuer de façon assez stable. Le problème vient donc du fait qu'on n'a pas suffisamment entrainé le modèle. Pour cela deux façons de corriger :

- Modifier le **learning rate** : rarement utile avec *adam*, risque d'ajouter de l'instabilité. A ne modifier que dans des cas extrèmes de stabilité ou vitesse de convergence.
- Modifier le **nombre d'époques**, c'est à dire le nombre de fois qu'on entraîne le réseau avec les données.

Ecrire le code pour entrainer le réseau avec 5 époques et des batchs de longueur 128 (voir la documentation sur la [méthode fit](https://keras.io/models/sequential/#fit)).

In [0]:
# Entrainer le réseau avec 5 époques
model.fit(X_train, y_train, batch_size=128, epochs=5)

# Calculer la précision
accuracy = model.evaluate(X_test, y_test)[1]
print("Précision : %.3f" % accuracy)

Ce premier de réseau de neurone simple nous a permis de reproduire un modèle de sci-kit learn avec keras. Mais l'avantage de keras, c'est qu'on peut aller beaucoup plus loin !

**Rajouter une ou plusieurs couches** denses et varier les paramètres si besoin afin d'entraîner l'algorithme à avoir une meilleure précision. 

**Attention :** il faut juger la précision sur les données test, et non sur les données d'entrainement.

*Conseil :* pour les couches intermédiaires, utiliser comme fonction d'activation `'relu'` ou `'sigmoid'`.

Pour tester la performance du modèle, essayez de l'entrainer sur moins de données : `X_train[:5000], y_train[:5000]` par exemple, ou moins.

In [0]:
# Création du modèle
# Créer un modèle séquentiel avec keras.models.Sequential()
< Compléter >

# Ajout des couches
< Compléter >

# Compiler le modèle
< Compléter >

# Entrainer le réseau
< Compléter >

# Evaluer le réseau
accuracy = model.evaluate(X_test, y_test)[1]
print("Précision : %.3f" % accuracy)

Nous avons donc vu :

- L'intérêt d'un réseau de neurone par rapport à des méthodes plus traditionelles
- Comment implémenter un réseau de neurones séquentiel avec Keras
- L'importance de la normalisation
- Quels sont les principaux paramètres d'entrainement d'un réseau de neurones et comment les régler
    - Fonction coût
    - Optimiseur
    - Epoques
    - Batches

Le plus dur étant de trouver la bonne structure du réseau de neurones permettant de résoudre le problème. A propos, la structure que nous avons utilisé n'est pas optimale...
 
## Limites de notre modèle

Le modèle que nous avons utilisé avec des couches denses n'est pas optimal pour résoudre notre problème, de plusieurs points de vue :

- Il ne prend pas en compte la position des pixels, il ne peut donc pas prendre en compte leur proximité, le fait qu'il y ait des lignes etc.
- Puisqu'il analyse tous les pixels indépendamment, il y a beaucoup de neurones redondants (pour détecter un motif en différents points de l'image, plusieurs neurones doivent effectuer des opérations similaires). Cela ralentit l'apprentissage et peut poser des problèmes d'overfitting.

Pour résoudre ces problèmes, on va donc utiliser des réseaux de neurones convolutifs, très utilisés dans l'analyse d'images...